# THREDDS-served GRIB Data: GFS (Global Grid) Model: Eclipse Cloud Cover Forecast

### This notebook reads in realtime GFS model output from a THREDDS server.

## Overview:
1. Determine latest available model run
1. Use dictionaries to deal with coordinate dimension names that change from run-to-run
1. Subset data and map regions
1. Create a 4-panel plot

## Imports

In [ ]:
import cartopy.crs as ccrs
import cartopy.feature as cfeature
from cartopy.io.shapereader import Reader
from matplotlib import pyplot as plt
from matplotlib.dates import DateFormatter, AutoDateLocator,HourLocator,DayLocator
from matplotlib.collections import LineCollection
from matplotlib.colors import BoundaryNorm, ListedColormap
import numpy as np
import xarray as xr
import pandas as pd
from datetime import datetime, timedelta
from pyproj import Proj
from metpy.plots import USCOUNTIES
import seaborn as sns
import geopandas as gpd
sns.set()

## Access real-time NWP data from Unidata's THREDDS server

Parse the current time and choose a recent hour when we might expect the model run to be complete. There is normally a ~90 minute lag, but we'll give it a bit more than that.

In [ ]:
now = datetime.now()
year = now.year
month = now.month
day = now.day
hour = now.hour
minute = now.minute


In [ ]:
# Allow for a six-hour lag between GFS initialization and current time
if (hour >= 18):
    runHour = 12
    hrDelta = hour - runHour
elif (hour >= 12):
    runHour = 6
    hrDelta = hour - runHour
elif (hour >= 6):
    runHour = 0
    hrDelta = hour - runHour
else:
    runHour = 18
    hrDelta = hour + 6
    
runTime = now - timedelta(hours=hrDelta)
runTimeStr = runTime.strftime('%Y%m%d %H00 UTC')
modelDate = runTime.strftime('%Y%m%d')
modelHour = runTime.strftime('%H')
modelMin = runTime.strftime('%M')
modelDay = runTime.strftime('%D')
titleTime = modelDay + ' ' +  modelHour + '00 UTC'
print (modelDay)
print (modelHour)
print (runTimeStr)
print(titleTime)

Open the most recent NCEP real-timeGFS from [Unidata's THREDDS server](https://thredds.ucar.edu/thredds/catalog/grib/NCEP/GFS/Global_0p25deg/catalog.html)

In [ ]:
ds = xr.open_dataset(f'https://thredds.ucar.edu/thredds/dodsC/grib/NCEP/GFS/Global_0p25deg/GFS_Global_0p25deg_{modelDate}_{modelHour}00.grib2')

In [ ]:
ds

Leverage MetPy's `parse_cf` function, which among other things will make it easy to extract the dataset's map projection.

In [ ]:
ds = ds.metpy.parse_cf()

In [ ]:
ds

Note that there now exists a `metpy_crs` coordinate variable, which we'll soon use to determine and use the `Dataset`'s map projection.

Select some of the variables from the `Dataset`; in this case, we'll choose those relating to cloud cover.

In [ ]:
varTotal = ds.Total_cloud_cover_entire_atmosphere
varLow = ds.Low_cloud_cover_low_cloud
varMed = ds.Medium_cloud_cover_middle_cloud
varHigh = ds.High_cloud_cover_high_cloud

Examine one of the grids

In [ ]:
varTotal

GRIB files that are served by THREDDS are [automatically converted into NetCDF](https://docs.unidata.ucar.edu/netcdf-java/5.5/userguide/grib_files_cdm.html). A quirk in this translation can result in certain dimensions (typically those that are *time* or *vertically*-based) varying from run-to-run. For example, the *time* coordinate dimension for a given variable might be `time` in one run, but `time1` (or `time2`, `time3`, etc.) in another run. This poses a challenge any time we want to subset a `DataArray`. For example, if a particular dataset had vertical levels in units of hPa, the dimension name for the geopotential height grid might be `isobaric`. If we wanted to select only the 500 and 700 hPa levels, we might write the following line of code:
```
Z = ds.sel(isobaric=[500, 700])
```

This would **fail** if we pointed to model output from a different time, and the vertical coordinate name for geopotential height was instead `isobaric1`.

Via strategic use of Python `dictionaries`, we can programmatically deal with this!

First, let's use some MetPy accessors that determine the dimension names for times and vertical levels:

In [ ]:
timeDim= varTotal.metpy.time.name
timeDim

We next construct `dictionaries` corresponding to each desired subset of the relevant dimensions. Here, we specify a desired date and time:

In [ ]:
verifTime = [datetime(2024, 4, 8, 18), datetime(2024, 4, 8, 21)]

timeDict = {timeDim: verifTime}

timeDict

Get the map projection from one of the `DataArray`s. They will be the same across the `Dataset`.

In [ ]:
proj_data = varTotal.metpy.cartopy_crs
proj_data

Create `DataArray` objects for the horizontal coordinate dimensions. In this case, the model is output on global cylindrical equidistant (PlateCarree) projection, which means the horizontal dimensions are named **lon** and **lat** and represent grid point locations in degrees.

In [ ]:
x, y = ds.lon, ds.lat

In [ ]:
x

## Subset the dataset to a smaller region

The longitudes range from 0 to 359.75 degrees East. For the purposes of selecting ranges which include points in the western hemisphere, express these values as positive numbers. The latitudes go from north to south ... i.e., in decreasing order.

In [ ]:
lonW, lonE, latS, latN = [-80 + 360, -71+360, 40, 45]
mapExtent = lonW, lonE, latS, latN

#### We can directly select latitude and longitude values to perform regional subset selections; no need to use the **Pyproj** library.

Determine the grid spacing

In [ ]:
delX, delY = ( (x[1] - x[0]), (y[1] - y[0]) )

In order for the data region to fill the plotted region, pad the longitude and latitude ranges (trial and error, depends on the subregion)

In [ ]:
xPad = 4
yPad = 4

xRange = np.arange(lonW - xPad, lonE + xPad, delX)
yRange = np.arange(latN + yPad, latS - yPad, delY)

Read in the subsetted data and coordinate variables.

In [ ]:
dsSub = ds.sel(lon = xRange, lat = yRange)
xSub, ySub = dsSub.lon, dsSub.lat

TotalSub = dsSub.Total_cloud_cover_entire_atmosphere
LowSub = dsSub.Low_cloud_cover_low_cloud
MedSub = dsSub.Medium_cloud_cover_middle_cloud
HighSub = dsSub.High_cloud_cover_high_cloud
TotalSub = TotalSub.sel(timeDict)
LowSub = LowSub.sel(timeDict)
MedSub = MedSub.sel(timeDict)
HighSub = HighSub.sel(timeDict)


Examine one of the `DataArray`s.

In [ ]:
HighSub

Specify the output map projection (Lambert Conformal, centered on New York State)

In [ ]:
lon1 = -75
lat1 = 42.5
slat = 42.5

proj_map= ccrs.LambertConformal(central_longitude=lon1,
                             central_latitude=lat1,
                             standard_parallels=[slat,slat])

In [ ]:
contourLevels = np.arange(0,101,10)

Create titles for the plots.

Create a 2x2 figure for each of the four cloud cover variables. Omit plotting the land/water features since they tend to obscure the nuances of the temperature field. This also speeds up the creation of the figure.

In [ ]:
for times in [0,1]:
#validTime = varTotal.sel(timeDict)[timeDim].values # Returns validTime as a NumPy Datetime 64 object
  validTime = TotalSub[timeDim][times].values # Returns validTime as a NumPy Datetime 64 object
  validTime = pd.Timestamp(validTime) # Converts validTime to a Pandas Timestamp object
  timeStr = validTime.strftime("%Y-%m-%d %H%M UTC") # We can now use Datetime's strftime method to create a time string.
  tlT1 = f"GFS Total Cloud Cover (%)"
  tlL1 = f"GFS Low Cloud Cover (%)"
  tlM1 = f"GFS Medium Cloud Cover (%)"
  tlH1 = f"GFS High Cloud Cover (%)"
  tl2 = str(f'Valid at: {timeStr}')
  title_line_total = (tlT1 + '\n' + tl2 + '\n')
  title_line_low = (tlL1 + '\n' + tl2 + '\n')
  title_line_med = (tlM1 + '\n' + tl2 + '\n')
  title_line_high = (tlH1 + '\n' + tl2 + '\n')

  res = '10m'
  fig = plt.figure(figsize=(18,12))

  ax1 = fig.add_subplot(2,2,1,projection=proj_map)
  ax1.set_extent (mapExtent, crs=ccrs.PlateCarree())
  ax1.add_feature (cfeature.COASTLINE.with_scale(res))
  ax1.add_feature (cfeature.STATES.with_scale(res))
  ax1.add_feature (USCOUNTIES,edgecolor='blue', linewidth=1 );
  CF = ax1.contourf (xSub,ySub,TotalSub[times], levels = contourLevels, cmap='Greys_r',alpha=0.5,transform=proj_data)
  cbar = fig.colorbar (CF, ax = ax1, fraction=0.046, pad=0.03,shrink=0.8)
  title = ax1.set_title(title_line_total,fontsize=16)

  ax2 = fig.add_subplot(2,2,2,projection=proj_map)
  ax2.set_extent (mapExtent, crs=ccrs.PlateCarree())
  ax2.add_feature (cfeature.COASTLINE.with_scale(res))
  ax2.add_feature (cfeature.STATES.with_scale(res))
  ax2.add_feature (USCOUNTIES,edgecolor='blue', linewidth=1 );
  CF = ax2.contourf (xSub,ySub,HighSub[times], levels = contourLevels, cmap='Greys_r',alpha=0.5,transform=proj_data)
  cbar = fig.colorbar (CF, ax = ax2, fraction=0.046, pad=0.03,shrink=0.8)
  title = ax2.set_title(title_line_high,fontsize=16)

  ax3 = fig.add_subplot(2,2,3,projection=proj_map)
  ax3.set_extent (mapExtent, crs=ccrs.PlateCarree())
  ax3.add_feature (cfeature.COASTLINE.with_scale(res))
  ax3.add_feature (cfeature.STATES.with_scale(res))
  ax3.add_feature (USCOUNTIES,edgecolor='blue', linewidth=1 );
  CF = ax3.contourf (xSub,ySub,MedSub[times], levels = contourLevels, cmap='Greys_r',alpha=0.5,transform=proj_data)
  cbar = fig.colorbar (CF, ax = ax3, fraction=0.046, pad=0.03,shrink=0.8)
  title = ax3.set_title(title_line_med,fontsize=16)

  ax4 = fig.add_subplot(2,2,4,projection=proj_map)
  ax4.set_extent (mapExtent, crs=ccrs.PlateCarree())
  ax4.add_feature (cfeature.COASTLINE.with_scale(res))
  ax4.add_feature (cfeature.STATES.with_scale(res))
  ax4.add_feature (USCOUNTIES,edgecolor='blue', linewidth=1 );
  CF = ax4.contourf (xSub,ySub,LowSub[times], levels = contourLevels, cmap='Greys_r',alpha=0.5,transform=proj_data)
  cbar = fig.colorbar (CF, ax = ax4, fraction=0.046, pad=0.03,shrink=0.8)
  title = ax4.set_title(title_line_low,fontsize=16);

  fig.tight_layout()
  plt.show()